In [1]:
from scipy import stats
import statistics
from sklearn import cluster
import pandas as pd
import matplotlib.pyplot as plt
plt.ioff()
import plotly.express as px
import plotly.graph_objects as go
import numpy as np
import random
import statsmodels.api as sm
import dash_bio as dashbio
from sklearn.linear_model import LinearRegression
from statsmodels.api import OLS
from statsmodels.graphics.gofplots import qqplot
import networkx as nx
import re
from scipy.cluster import hierarchy
from progressbar import ProgressBar, Percentage, Bar

In [21]:
import warnings
warnings.filterwarnings("ignore", message="divide by zero encountered in double_scalars")
warnings.filterwarnings("ignore", message="highly fragmented")

In [22]:
genus = pd.read_csv('data/genus.csv')
behavior = pd.read_csv('data/behaviors.csv')

In [23]:
predict = random.choice(behavior.columns)

In [24]:
behavior.shape

(378, 35)

In [25]:
treeDF = pd.read_csv('data/summary_tree.csv')

In [26]:
def title_format(variable):
    return ("_").join(variable.split("_")[1:]).replace("_batch_ranknorm","").replace("pct","%").replace("_"," ").title()

In [27]:
def test_normality(d, alpha=0.01):
    """
    Return true if suspected normal
    Return false if suspected non-normal
    """
    k2, p = stats.normaltest(d)
    if p < alpha:  # null hypothesis: x comes from a normal distribution
        #print("The null hypothesis can be rejected")
        return False
    else:
        #print("The null hypothesis cannot be rejected")
        return True

In [28]:
def make_QQ(d, title='MISSING', alpha=0.01):
    
    qqplot_data = qqplot(d, line='s').gca().lines;
    
    isNormal = test_normality(d, alpha=alpha)
    
    fig = go.Figure()

    fig.add_trace({
        'type': 'scatter',
        'x': qqplot_data[0].get_xdata(),
        'y': qqplot_data[0].get_ydata(),
        'mode': 'markers',
        'marker': {
            'color': '#19d3f3'
        }
    })

    fig.add_trace({
        'type': 'scatter',
        'x': qqplot_data[1].get_xdata(),
        'y': qqplot_data[1].get_ydata(),
        'mode': 'lines',
        'line': {
            'color': 'red'
        }

    })


    fig['layout'].update({
        'title': f"QQ Plot of {title.replace('g__','').replace('_',' ')}<br>Suspected {'Normal' if isNormal else 'Not Normal'} at Alpha {alpha}",
        'xaxis': {
            'title': 'Theoretical Quantiles',
            'zeroline': False
        },
        'yaxis': {
            'title': 'Sample Quantiles'
        },
        'showlegend': False,
        'width': 500,
        'height': 450,
        'template': 'plotly_white'
    })
    
    fig.write_image(f"images/QQ_{title}.png")
    return fig

In [29]:
%%capture
for g in genus.columns:
    make_QQ(genus[g], title=g)

In [30]:
normals = 0
nonnormal = 0
for g in genus.columns:
    isNormal = test_normality(genus[g])
    if isNormal:
        normals +=1
    else:
        nonnormal +=1
print(f'Normal: {normals}, Non-Normal: {nonnormal}')

Normal: 35, Non-Normal: 147


In [31]:
def binarize(df, debug=False):
    newDF = df.copy().drop(columns=df.columns)
    for d in df:
        isNormal = test_normality(df[d])
        mode = statistics.mode(df[d])
        modecount = list(df[d]).count(mode)
        if debug:
            print(f"{d} is {'Normal' if isNormal else 'Not Normal'}")
            print(f'Mode {mode} appears {modecount} times in {d}\n')
        if isNormal:
            newDF[d] = df[d]
        if not isNormal:
            newDF[d] = [0 if v==mode else 1 for v in df[d]]       
    return newDF

In [32]:
binarized = binarize(genus)

/var/folders/n9/2xpxt3jn6nj70w3trry_qn080000gn/T/ipykernel_98597/3667768557.py:13: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

/var/folders/n9/2xpxt3jn6nj70w3trry_qn080000gn/T/ipykernel_98597/3667768557.py:13: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

/var/folders/n9/2xpxt3jn6nj70w3trry_qn080000gn/T/ipykernel_98597/3667768557.py:13: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd

In [33]:
def dendrogram(df,ascending=False,title="Comparison of Microbe Pairs<br>by Co-Occurrence", append=''):

    matrix = df.T.dot(df)
    columns = list(matrix.columns.values)
    rows = list(matrix.index)

    fig = px.imshow(matrix, color_continuous_scale='blues', width=800, height=800, title=title)
    fig.update(layout_coloraxis_showscale=False)
    fig.write_image(f'images/matrix{append}.png')
    return fig

In [34]:
dendrogram(binarize(genus), title="Comparison of Binarized Microbe Pairs<br>by Co-Occurrence", append='_binarized')

/var/folders/n9/2xpxt3jn6nj70w3trry_qn080000gn/T/ipykernel_98597/3667768557.py:13: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

/var/folders/n9/2xpxt3jn6nj70w3trry_qn080000gn/T/ipykernel_98597/3667768557.py:13: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`

/var/folders/n9/2xpxt3jn6nj70w3trry_qn080000gn/T/ipykernel_98597/3667768557.py:13: PerformanceWarning:

DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd

In [35]:
def get_tree_occur():
    treeLookup = {}
    for b in list(behavior.columns):
        subDF = treeDF[treeDF['behavior']==b]
        microbes = list(subDF['source'])
        microbes.extend(list(subDF['target']))
        microbes = list(set(microbes))
        treeLookup[b] = microbes
    occurDF = pd.DataFrame(columns=list(behavior.columns), index=list(genus.columns))
    for b in list(behavior.columns):
        occurDF[b] = [(1 if g in treeLookup[b] else 0) for g in list(genus.columns)]
    return occurDF.T

In [36]:
dendrogram(get_tree_occur(), title="Comparison of All Microbe Pairs<br>by Tree Co-Occurrence", append='_tree_co-occurrence')

In [37]:
def get_coDF(min_co=5):
    df = get_tree_occur()
    matrix = df.T.dot(df)
    mask = np.triu(np.ones(df.shape)).astype(bool)
    matrix = matrix.where(np.triu(np.ones(matrix.shape)).astype(bool))
    occurEdges = pd.DataFrame(matrix.unstack(level=1)).reset_index()
    occurEdges.columns = ['source','target','co']
    occurEdges = occurEdges[occurEdges['source'] != occurEdges['target']]
    occurEdges = occurEdges[occurEdges['co']>min_co]
    occurEdges = occurEdges.sort_values(by='co', ascending=False).reset_index().drop(columns='index')
    print(occurEdges.shape)
    return occurEdges

In [38]:
def compute_interactions(df, min_co=5):
    newDF = df.copy().drop(columns=df.columns)
    coDF = get_coDF(min_co=min_co)
    for index, row in coDF.iterrows():
        s = row['source']
        t = row['target']
        newDF[f'int_{s}_*_{t}'] = list(df[s]*df[t])
    return newDF

In [39]:
def fit_model(df, debug=True, summarize=False):
    X = df
    y = behavior[predict]
    model = LinearRegression().fit(X, y)
    R2 = model.score(X, y)
    mod = OLS(y,X).fit()
    fstat = mod.summary2().tables[0][3][4]
    if debug:
        print(f'Fitting a model on {X.shape[1]} features for {X.shape[0]} observations...')
        print(f'Predicting {title_format(predict)}...')
        print(f'Score: {R2}') #print(f'Score: ~{np.round(R2, 5)}')
        print(f'F-stat: {fstat}')
        print(f'...this means that {np.round(R2*100,2)}% of the variation in {title_format(predict)}\ncan be explained by the {X.shape[1]} predictor variables in the model.\n')
    mod = OLS(y,X).fit()
    results = {
        'intercept' : model.intercept_,
        'coef' : model.coef_,
        'score' : R2,
        'f': mod.summary2().tables[0][3][4],
        'df': mod.summary2().tables[0][1][4],
        'p_values': mod.summary2().tables[1]['P>|t|'],
        'summary': mod.summary2()
    }
    return model, results

In [40]:
def make_prediction(df, model):
    yhat = model.predict(df)
    y=behavior[predict]
    residual = [(act-pred) for act, pred in zip(y,yhat)]
    predDF = pd.DataFrame()
    predDF['pred'] = yhat
    predDF['act'] = list(y)
    predDF['res'] = residual
    return predDF

In [41]:
def run_test(df, title, debug=True):
    model, summary = fit_model(df, debug=debug, summarize=True)
    predDF = make_prediction(df, model)
    if debug:
        residual = make_QQ(predDF['res'], title=f'Residuals of {title}')
        return summary, residual
    else:
        return summary, None

In [47]:
base_tests = [
    {'df':genus, 'title':'Kitchen Sink'},
    {'df':binarized, 'title':'Binarized'},
    {'df':compute_interactions(genus, min_co=1), 'title':'Interactions'},
    {'df':compute_interactions(binarized, min_co=1), 'title':'Binarized Interactions'},
]

(90, 3)
(90, 3)


In [48]:
def run_tests(tests, debug=True, baseline=0.16555759872515363):
    summary = pd.DataFrame(columns=['test','n','R2'])
    pbar = ProgressBar(widgets=[Percentage(), Bar()], maxval=len(tests)).start()
    for i, t in enumerate(tests):
        test_summary, residual = run_test(t['df'], t['title'], debug=debug)
        result = pd.DataFrame({'test': t['title'], 'n': t['df'].shape[1], 'R2': test_summary['score']}, index=[0])
        summary = pd.concat([summary, result], ignore_index = True)
        if debug: residual.show()
        pbar.update(i+1)
    pbar.finish()
    summary['R2_diff'] = [(baseline - r) for r in summary['R2']]
    return summary

In [49]:
baseline = run_tests(base_tests, debug=True)

Fitting a model on 182 features for 378 observations...
Predicting Lectureship...
Score: 0.5061924289162895
F-stat: 2.833
...this means that 50.62% of the variation in Lectureship
can be explained by the 182 predictor variables in the model.



Fitting a model on 182 features for 378 observations...
Predicting Lectureship...
Score: 0.10623237995393975
F-stat: 11.88
...this means that 10.62% of the variation in Lectureship
can be explained by the 182 predictor variables in the model.



Fitting a model on 90 features for 378 observations...
Predicting Lectureship...
Score: 0.20449542840467172
F-stat: 3.431
...this means that 20.45% of the variation in Lectureship
can be explained by the 90 predictor variables in the model.



Fitting a model on 90 features for 378 observations...
Predicting Lectureship...
Score: 0.035966192798128516
F-stat: 24.38
...this means that 3.6% of the variation in Lectureship
can be explained by the 90 predictor variables in the model.



100%|##########################################################################|


In [50]:
baseline

test    n        R2   R2_diff
0            Kitchen Sink  182  0.506192 -0.340635
1               Binarized  182  0.106232  0.059325
2            Interactions   90  0.204495 -0.038938
3  Binarized Interactions   90  0.035966  0.129591

In [51]:
px.scatter(baseline, x='n', y='R2', hover_data=['test'])

In [52]:
def remove_q(q):
    subset = genus.copy()
    subset.drop(q, axis=1)
    dropout_tests.append({'df':subset, 'title':f'Dropped {q}'})

In [53]:
dropout_tests = []

In [54]:
for q in genus.columns:
    remove_q(q)

In [55]:
dropoutDF = run_tests(dropout_tests, debug=False)

100%|##########################################################################|


In [56]:
dropoutDF = dropoutDF.sort_values(by=['R2_diff'], ascending=False).reset_index().drop(columns='index')

In [57]:
px.scatter(dropoutDF, dropoutDF.index, 'R2_diff')

In [58]:
def get_edges(df):
    mask = np.triu(np.ones(df.shape)).astype(bool)
    matrix = df.T.dot(df)
    matrix = matrix.where(np.triu(np.ones(matrix.shape)).astype(bool))
    occurEdges = pd.DataFrame(matrix.unstack(level=1)).reset_index()
    occurEdges.columns = ['source','target','co']
    occurEdges = occurEdges.drop(columns='co')
    occurEdges = occurEdges[occurEdges['source'] != occurEdges['target']]
    return occurEdges

In [59]:
interaction_tests = []

In [60]:
def only_int(i, j, df):
    subset = binarized.copy()
    subset = subset.filter([i,j])
    subset['ij'] = subset[i]*subset[j]
    interaction_tests.append({'df':subset, 'title':f'{i}*{j}'})

In [61]:
edges = get_edges(genus)

In [62]:
for i, row in edges.iterrows():
    only_int(row['source'], row['target'], genus)

In [63]:
interaction_results = run_tests(interaction_tests, debug=False)

100%|##########################################################################|


In [64]:
interaction_results = interaction_results.sort_values(by='R2', ascending=False).reset_index().drop(columns='index')

In [65]:
ij = interaction_results['test'].str.split('*', expand=True)
ij.columns = ['i','j']
interaction_results = pd.concat([interaction_results, ij], axis=1)

In [66]:
interaction_results

test  n        R2   R2_diff              i  \
0       g__sit*g__architecto  3  0.034073  0.131485         g__sit   
1       g__architecto*g__sit  3  0.034073  0.131485  g__architecto   
2          g__sit*g__aperiam  3  0.031635  0.133922         g__sit   
3          g__aperiam*g__sit  3  0.031635  0.133922     g__aperiam   
4             g__ipsa*g__sit  3  0.031503  0.134054        g__ipsa   
...                      ... ..       ...       ...            ...   
32937  g__quidem*g__voluptas  3  0.000157  0.165401      g__quidem   
32938          g__nam*g__eos  3  0.000095  0.165463         g__nam   
32939          g__eos*g__nam  3  0.000095  0.165463         g__eos   
32940        g__ipsa*g__iure  3  0.000093  0.165465        g__ipsa   
32941        g__iure*g__ipsa  3  0.000093  0.165465        g__iure   

                   j  
0      g__architecto  
1             g__sit  
2         g__aperiam  
3             g__sit  
4             g__sit  
...              ...  
32937    g__voluptas  
32938         g__eos  
32939         g__nam  
32940        g__iure  
32941        g__ipsa  

[32942 rows x 6 columns]

In [67]:
fig = px.scatter(interaction_results,
                 x=interaction_results.index,
                 y='R2',
                 log_x=True,
                 hover_data=['i','j'],
                 title='R2 of interactions for simple i + j + ij',
                 width=600,
                 height=500
                )
fig.update_layout(template='plotly_white')
fig.show()

In [68]:
i,j = interaction_results.iloc[0]['i'], interaction_results.iloc[0]['j']

In [69]:
interaction_results

test  n        R2   R2_diff              i  \
0       g__sit*g__architecto  3  0.034073  0.131485         g__sit   
1       g__architecto*g__sit  3  0.034073  0.131485  g__architecto   
2          g__sit*g__aperiam  3  0.031635  0.133922         g__sit   
3          g__aperiam*g__sit  3  0.031635  0.133922     g__aperiam   
4             g__ipsa*g__sit  3  0.031503  0.134054        g__ipsa   
...                      ... ..       ...       ...            ...   
32937  g__quidem*g__voluptas  3  0.000157  0.165401      g__quidem   
32938          g__nam*g__eos  3  0.000095  0.165463         g__nam   
32939          g__eos*g__nam  3  0.000095  0.165463         g__eos   
32940        g__ipsa*g__iure  3  0.000093  0.165465        g__ipsa   
32941        g__iure*g__ipsa  3  0.000093  0.165465        g__iure   

                   j  
0      g__architecto  
1             g__sit  
2         g__aperiam  
3             g__sit  
4             g__sit  
...              ...  
32937    g__voluptas  
32938         g__eos  
32939         g__nam  
32940        g__iure  
32941        g__ipsa  

[32942 rows x 6 columns]

In [70]:
def visualize_prediction(df, model, residual = False, add='', predDF=None):
    if predDF is None:
        predDF = make_prediction(df, model)
    fig = px.scatter(x=predDF['pred'] if residual else predDF['act'],
                     y=predDF['res'] if residual else predDF['pred'],
                     labels=dict(y='Residual' if residual else 'Predicted', x='Predicted' if residual else 'Actual'),
                     color=predDF['res'],
                     #trendline="ols",
                     color_continuous_scale="rdbu",
                     range_color=[-max(predDF['res']),max(predDF['res'])],
                     title=f"{'Predicted' if residual else 'Actual'} vs. {'Residual' if residual else 'Predicted'} Values for <br>{title_format(df.columns[-1])} {add}"
                    )
    fig.update_traces(marker=dict(size=12,
                              line=dict(width=1,
                                        color='DarkSlateGrey'),
                                opacity=0.8)
                     )
    results = px.get_trendline_results(fig)
    #results.px_fit_results.iloc[0].summary()
    fig.update_layout(
        template='plotly_white',
        width=700,
        coloraxis_showscale=False
    )
    if not residual:
        fig.add_shape(
            type="line", line=dict(dash='dash'),
            x0=predDF['act'].min(), y0=predDF['act'].min(),
            x1=predDF['act'].max(), y1=predDF['act'].max()
        )
    fig.write_image(f'preds/{"residual" if residual else "predicted"}-vs-actual_{i}_vs_{j}.png')
    return fig

In [71]:
def visualize_prediction_ij(i,j):
    df = binarized.filter([i,j])
    df[f'{i} * {j}'] = df[i]*df[j]
    model, summary = fit_model(df, debug=True, summarize=False)
    predDF = make_prediction(df, model)
    predviz = visualize_prediction(df, model, residual=False, add=f'{i} vs. {j}', predDF = predDF)
    resviz = visualize_prediction(df, model, residual=True, add=f'{i} vs. {j}', predDF = predDF)
    qq_res = make_QQ(predDF['res'], title=f'Residuals of<br>{i} vs. {j}')
    return predviz, resviz, qq_res

In [72]:
def visualize_top_n_interactions(n=5, debug=True):
    for r in range(0,n):
        i,j = interaction_results.iloc[r]['i'], interaction_results.iloc[r]['j']
        print(i,j)
        predviz, resviz, qq_res = visualize_prediction_ij(i,j)
        if debug:
            for chart in [predviz, resviz, qq_res]:
                chart.show()

In [73]:
visualize_top_n_interactions(n=5, debug=False)

g__sit g__architecto
Fitting a model on 3 features for 378 observations...
Predicting Lectureship...
Score: 0.03407261782272464
F-stat: 89.56
...this means that 3.41% of the variation in Lectureship
can be explained by the 3 predictor variables in the model.

g__architecto g__sit
Fitting a model on 3 features for 378 observations...
Predicting Lectureship...
Score: 0.03407261782272464
F-stat: 89.56
...this means that 3.41% of the variation in Lectureship
can be explained by the 3 predictor variables in the model.

g__sit g__aperiam
Fitting a model on 3 features for 378 observations...
Predicting Lectureship...
Score: 0.03163539122385761
F-stat: 52.93
...this means that 3.16% of the variation in Lectureship
can be explained by the 3 predictor variables in the model.

g__aperiam g__sit
Fitting a model on 3 features for 378 observations...
Predicting Lectureship...
Score: 0.03163539122385761
F-stat: 52.93
...this means that 3.16% of the variation in Lectureship
can be explained by the 3 p